# 101 Formulaic Alphas - Implementation + Backtests

This notebook implements the 101 formulaic alphas from `101_alphas.pdf` (Kakushadze) and runs each alpha through the repo's regular backtester.

Notes / Adaptations:
- Data source: repo OHLCV from `dataset/cleaned` (100 assets).
- VWAP is approximated using typical price `(High+Low+Close)/3` (intraday VWAP is not available in this dataset).
- Any industry/sector neutralization in the original formulas is treated as cross-sectional de-meaning (no sector/industry data available).

Outputs per alpha:
- Backtest statistics (`compute_backtest_report`)
- Existing Bokeh dashboard (`build_interactive_portfolio_layout`)


In [11]:
from __future__ import annotations

from pathlib import Path
import sys

import numpy as np
import pandas as pd

from bokeh.io import output_notebook, show



In [12]:
# Resolve project root robustly
CWD = Path.cwd().resolve()
PROJECT_ROOT = None
for p in [CWD, *CWD.parents]:
    if (p / 'dataset').exists() and (p / 'src').exists():
        PROJECT_ROOT = p
        break
if PROJECT_ROOT is None:
    raise RuntimeError(f'Could not locate project root from CWD={CWD}')
if str(PROJECT_ROOT) not in sys.path:
    sys.path.insert(0, str(PROJECT_ROOT))
    import os
    os.chdir(PROJECT_ROOT)
print('PROJECT_ROOT:', PROJECT_ROOT)

from src.backtester.data import load_cleaned_assets, align_close_prices
from src.backtester.engine import BacktestConfig, run_backtest
from src.backtester.report import compute_backtest_report
from src.backtester.bokeh_plots import build_interactive_portfolio_layout



PROJECT_ROOT: /home/anivarth/college/quant-task


In [13]:
# Load OHLCV
assets_ohlcv = load_cleaned_assets(cleaned_dir=str(PROJECT_ROOT / 'dataset' / 'cleaned'))

close = align_close_prices(assets_ohlcv).sort_index().ffill().bfill()
open_ = pd.concat([df['Open'].astype(float).rename(sym) for sym, df in assets_ohlcv.items()], axis=1).reindex(close.index).ffill().bfill()
high = pd.concat([df['High'].astype(float).rename(sym) for sym, df in assets_ohlcv.items()], axis=1).reindex(close.index).ffill().bfill()
low = pd.concat([df['Low'].astype(float).rename(sym) for sym, df in assets_ohlcv.items()], axis=1).reindex(close.index).ffill().bfill()
volume = pd.concat([df['Volume'].astype(float).rename(sym) for sym, df in assets_ohlcv.items()], axis=1).reindex(close.index).fillna(0.0)

# VWAP proxy (intraday VWAP not available)
vwap = (high + low + close) / 3.0

# Returns (close-to-close)
returns = close.pct_change().fillna(0.0)

# ADV series
def adv(x: pd.DataFrame, d: int) -> pd.DataFrame:
    return x.rolling(d, min_periods=1).mean()

adv5 = adv(volume, 5)
adv10 = adv(volume, 10)
adv15 = adv(volume, 15)
adv20 = adv(volume, 20)
adv30 = adv(volume, 30)
adv40 = adv(volume, 40)
adv50 = adv(volume, 50)
adv60 = adv(volume, 60)
adv81 = adv(volume, 81)
adv120 = adv(volume, 120)
adv150 = adv(volume, 150)
adv180 = adv(volume, 180)

# Cap proxy
cap = close * volume

# Aliases matching ML4T notebook variable names
c = close.copy()
o = open_.copy()
h = high.copy()
l = low.copy()
v = volume.copy()
r = returns.copy()
# Ensure column level name matches ML4T alpha code expectations
for _df in [close, open_, high, low, volume, vwap, returns, cap, c, o, h, l, v, r]:
    _df.columns.name = 'ticker'


print('close shape:', close.shape)
print('date range:', close.index.min().date(), '->', close.index.max().date())


close shape: (2511, 100)
date range: 2016-01-25 -> 2026-01-16


In [14]:
# Market proxy OHLCV for Bokeh
market_df = pd.DataFrame({
    'Open': open_.mean(axis=1),
    'High': high.mean(axis=1),
    'Low': low.mean(axis=1),
    'Close': close.mean(axis=1),
    'Volume': volume.sum(axis=1),
}).sort_index()


In [15]:
def rank(df):
    """Return the cross-sectional percentile rank

     Args:
         :param df: tickers in columns, sorted dates in rows.

     Returns:
         pd.DataFrame: the ranked values
     """
    return df.rank(axis=1, pct=True)

def scale(df):
    """
    Scaling time serie.
    :param df: a pandas DataFrame.
    :param k: scaling factor.
    :return: a pandas DataFrame rescaled df such that sum(abs(df)) = k
    """
    return df.div(df.abs().sum(axis=1), axis=0)

def log(df):
    return np.log1p(df)

def sign(df):
    return np.sign(df)

def power(df, exp):
    return df.pow(exp)

def ts_lag(df: pd.DataFrame, t: int = 1) -> pd.DataFrame:
    """Return the lagged values t periods ago.

    Args:
        :param df: tickers in columns, sorted dates in rows.
        :param t: lag

    Returns:
        pd.DataFrame: the lagged values
    """
    return df.shift(t)

def ts_delta(df, period=1):
    """
    Wrapper function to estimate difference.
    :param df: a pandas DataFrame.
    :param period: the difference grade.
    :return: a pandas DataFrame with today’s value minus the value 'period' days ago.
    """
    return df.diff(period)

def ts_sum(df: pd.DataFrame, window: int = 10) -> pd.DataFrame:
    """Computes the rolling ts_sum for the given window size.

    Args:
        df (pd.DataFrame): tickers in columns, dates in rows.
        window      (int): size of rolling window.

    Returns:
        pd.DataFrame: the ts_sum over the last 'window' days.
    """
    return df.rolling(window).sum()

def ts_mean(df, window=10):
    """Computes the rolling mean for the given window size.

    Args:
        df (pd.DataFrame): tickers in columns, dates in rows.
        window      (int): size of rolling window.

    Returns:
        pd.DataFrame: the mean over the last 'window' days.
    """
    return df.rolling(window).mean()

def ts_weighted_mean(df, period=10):
    """
    Linear weighted moving average implementation.
    :param df: a pandas DataFrame.
    :param period: the LWMA period
    :return: a pandas DataFrame with the LWMA.
    """
    return (df.apply(lambda x: WMA(x, timeperiod=period)))

def ts_std(df, window=10):
    """
    Wrapper function to estimate rolling standard deviation.
    :param df: a pandas DataFrame.
    :param window: the rolling window.
    :return: a pandas DataFrame with the time-series min over the past 'window' days.
    """
    return (df
            .rolling(window)
            .std())

def ts_rank(df, window=10):
    """
    Wrapper function to estimate rolling rank.
    :param df: a pandas DataFrame.
    :param window: the rolling window.
    :return: a pandas DataFrame with the time-series rank over the past window days.
    """
    return (df
            .rolling(window)
            .apply(lambda x: x.rank().iloc[-1]))

def ts_product(df, window=10):
    """
    Wrapper function to estimate rolling ts_product.
    :param df: a pandas DataFrame.
    :param window: the rolling window.
    :return: a pandas DataFrame with the time-series ts_product over the past 'window' days.
    """
    return (df
            .rolling(window)
            .apply(np.prod))

def ts_min(df, window=10):
    """
    Wrapper function to estimate rolling min.
    :param df: a pandas DataFrame.
    :param window: the rolling window.
    :return: a pandas DataFrame with the time-series min over the past 'window' days.
    """
    return df.rolling(window).min()

def ts_max(df, window=10):
    """
    Wrapper function to estimate rolling min.
    :param df: a pandas DataFrame.
    :param window: the rolling window.
    :return: a pandas DataFrame with the time-series max over the past 'window' days.
    """
    return df.rolling(window).max()

def ts_argmax(df, window=10):
    """
    Wrapper function to estimate which day ts_max(df, window) occurred on
    :param df: a pandas DataFrame.
    :param window: the rolling window.
    :return: well.. that :)
    """
    return df.rolling(window).apply(np.argmax).add(1)

def ts_argmin(df, window=10):
    """
    Wrapper function to estimate which day ts_min(df, window) occurred on
    :param df: a pandas DataFrame.
    :param window: the rolling window.
    :return: well.. that :)
    """
    return (df.rolling(window)
            .apply(np.argmin)
            .add(1))

def ts_corr(x, y, window=10):
    """
    Wrapper function to estimate rolling correlations.
    :param x, y: pandas DataFrames.
    :param window: the rolling window.
    :return: a pandas DataFrame with the time-series min over the past 'window' days.
    """
    return x.rolling(window).corr(y)

def ts_cov(x, y, window=10):
    """
    Wrapper function to estimate rolling covariance.
    :param df: a pandas DataFrame.
    :param window: the rolling window.
    :return: a pandas DataFrame with the time-series min over the past 'window' days.
    """
    return x.rolling(window).cov(y)

def alpha001(c, r):
    """(rank(ts_argmax(power(((returns < 0)
        ? ts_std(returns, 20)
        : close), 2.), 5)) -0.5)"""
    c[r < 0] = ts_std(r, 20)
    return (rank(ts_argmax(power(c, 2), 5)).mul(-.5)
            .stack().swaplevel())

def alpha002(o, c, v):
    """(-1 * ts_corr(rank(ts_delta(log(volume), 2)), rank(((close - open) / open)), 6))"""
    s1 = rank(ts_delta(log(v), 2))
    s2 = rank((c / o) - 1)
    alpha = -ts_corr(s1, s2, 6)
    return alpha.stack('ticker').swaplevel().replace([-np.inf, np.inf], np.nan)

def alpha003(o, v):
    """(-1 * ts_corr(rank(open), rank(volume), 10))"""

    return (-ts_corr(rank(o), rank(v), 10)
            .stack('ticker')
            .swaplevel()
            .replace([-np.inf, np.inf], np.nan))

def alpha004(l):
    """(-1 * Ts_Rank(rank(low), 9))"""
    return (-ts_rank(rank(l), 9)
            .stack('ticker')
            .swaplevel())

def alpha005(o, vwap, c):
    """(rank((open - ts_mean(vwap, 10))) * (-1 * abs(rank((close - vwap)))))"""
    return (rank(o.sub(ts_mean(vwap, 10)))
            .mul(rank(c.sub(vwap)).mul(-1).abs())
            .stack('ticker')
            .swaplevel())

def alpha006(o, v):
    """(-ts_corr(open, volume, 10))"""
    return (-ts_corr(o, v, 10)
            .stack('ticker')
            .swaplevel())

def alpha007(c, v, adv20):
    """(adv20 < volume) 
        ? ((-ts_rank(abs(ts_delta(close, 7)), 60)) * sign(ts_delta(close, 7))) 
        : -1
    """
    
    delta7 = ts_delta(c, 7)
    return (-ts_rank(abs(delta7), 60)
            .mul(sign(delta7))
            .where(adv20<v, -1)
            .stack('ticker')
            .swaplevel())

def alpha008(o, r):
    """-rank(((ts_sum(open, 5) * ts_sum(returns, 5)) - 
        ts_lag((ts_sum(open, 5) * ts_sum(returns, 5)),10)))
    """
    return (-(rank(((ts_sum(o, 5) * ts_sum(r, 5)) -
                       ts_lag((ts_sum(o, 5) * ts_sum(r, 5)), 10))))
           .stack('ticker')
            .swaplevel())

def alpha009(c):
    """(0 < ts_min(ts_delta(close, 1), 5)) ? ts_delta(close, 1) 
    : ((ts_max(ts_delta(close, 1), 5) < 0) 
    ? ts_delta(close, 1) : (-1 * ts_delta(close, 1)))
    """
    close_diff = ts_delta(c, 1)
    alpha = close_diff.where(ts_min(close_diff, 5) > 0,
                             close_diff.where(ts_max(close_diff, 5) < 0,
                                              -close_diff))
    return (alpha
            .stack('ticker')
            .swaplevel())

def alpha010(c):
    """rank(((0 < ts_min(ts_delta(close, 1), 4)) 
        ? ts_delta(close, 1) 
        : ((ts_max(ts_delta(close, 1), 4) < 0)
            ? ts_delta(close, 1) 
            : (-1 * ts_delta(close, 1)))))
    """
    close_diff = ts_delta(c, 1)
    alpha = close_diff.where(ts_min(close_diff, 4) > 0,
                             close_diff.where(ts_min(close_diff, 4) > 0,
                                              -close_diff))

    return (rank(alpha)
            .stack('ticker')
            .swaplevel())

def alpha011(c, vwap, v):
    """(rank(ts_max((vwap - close), 3)) + 
        rank(ts_min(vwap - close), 3)) * 
        rank(ts_delta(volume, 3))
        """
    return (rank(ts_max(vwap.sub(c), 3))
            .add(rank(ts_min(vwap.sub(c), 3)))
            .mul(rank(ts_delta(v, 3)))
            .stack('ticker')
            .swaplevel())

def alpha012(v, c):
    """(sign(ts_delta(volume, 1)) * 
            (-1 * ts_delta(close, 1)))
        """
    return (sign(ts_delta(v, 1)).mul(-ts_delta(c, 1))
            .stack('ticker')
            .swaplevel())

def alpha013(c, v):
    """-rank(ts_cov(rank(close), rank(volume), 5))"""
    return (-rank(ts_cov(rank(c), rank(v), 5))
            .stack('ticker')
            .swaplevel())

def alpha014(o, v, r):
    """
    (-rank(ts_delta(returns, 3))) * ts_corr(open, volume, 10))
    """

    alpha = -rank(ts_delta(r, 3)).mul(ts_corr(o, v, 10)
                                      .replace([-np.inf,
                                                np.inf],
                                               np.nan))
    return (alpha
            .stack('ticker')
            .swaplevel())

def alpha015(h, v):
    """(-1 * ts_sum(rank(ts_corr(rank(high), rank(volume), 3)), 3))"""
    alpha = (-ts_sum(rank(ts_corr(rank(h), rank(v), 3)
                          .replace([-np.inf, np.inf], np.nan)), 3))
    return (alpha
            .stack('ticker')
            .swaplevel())

def alpha016(h, v):
    """(-1 * rank(ts_cov(rank(high), rank(volume), 5)))"""
    return (-rank(ts_cov(rank(h), rank(v), 5))
            .stack('ticker')
            .swaplevel())

def alpha017(c, v):
    """(((-1 * rank(ts_rank(close, 10))) * rank(ts_delta(ts_delta(close, 1), 1))) *rank(ts_rank((volume / adv20), 5)))
        """
    adv20 = ts_mean(v, 20)
    return (-rank(ts_rank(c, 10))
            .mul(rank(ts_delta(ts_delta(c, 1), 1)))
            .mul(rank(ts_rank(v.div(adv20), 5)))
            .stack('ticker')
            .swaplevel())

def alpha018(o, c):
    """-rank((ts_std(abs((close - open)), 5) + (close - open)) +
            ts_corr(close, open,10))
    """
    return (-rank(ts_std(c.sub(o).abs(), 5)
                  .add(c.sub(o))
                  .add(ts_corr(c, o, 10)
                       .replace([-np.inf,
                                 np.inf],
                                np.nan)))
            .stack('ticker')
            .swaplevel())

def alpha019(c, r):
    """((-1 * sign(((close - ts_lag(close, 7)) + ts_delta(close, 7)))) * 
    (1 + rank((1 + ts_sum(returns,250)))))
    """
    return (-sign(ts_delta(c, 7) + ts_delta(c, 7))
            .mul(1 + rank(1 + ts_sum(r, 250)))
            .stack('ticker')
            .swaplevel())

def alpha020(o, h, l, c):
    """-rank(open - ts_lag(high, 1)) * 
        rank(open - ts_lag(close, 1)) * 
        rank(open -ts_lag(low, 1))"""
    return (rank(o - ts_lag(h, 1))
            .mul(rank(o - ts_lag(c, 1)))
            .mul(rank(o - ts_lag(l, 1)))
            .mul(-1)
            .stack('ticker')
            .swaplevel())

def alpha021(c, v):
    """ts_mean(close, 8) + ts_std(close, 8) < ts_mean(close, 2)
        ? -1
        : (ts_mean(close,2) < ts_mean(close, 8) - ts_std(close, 8)
            ? 1
            : (volume / adv20 < 1
                ? -1
                : 1))
    """
    sma2 = ts_mean(c, 2)
    sma8 = ts_mean(c, 8)
    std8 = ts_std(c, 8)

    cond_1 = sma8.add(std8) < sma2
    cond_2 = sma8.add(std8) > sma2
    cond_3 = v.div(ts_mean(v, 20)) < 1

    val = np.ones_like(c)
    alpha = pd.DataFrame(np.select(condlist=[cond_1, cond_2, cond_3],
                                   choicelist=[-1, 1, -1], default=1),
                         index=c.index,
                         columns=c.columns)

    return (alpha
            .stack('ticker')
            .swaplevel())

def alpha022(h, c, v):
    """-(ts_delta(ts_corr(high, volume, 5), 5) * 
        rank(ts_std(close, 20)))
    """

    return (ts_delta(ts_corr(h, v, 5)
                     .replace([-np.inf,
                               np.inf],
                              np.nan), 5)
            .mul(rank(ts_std(c, 20)))
            .mul(-1)
            .stack('ticker')
            .swaplevel())

def alpha023(h, c):
    """((ts_mean(high, 20) < high)
            ? (-1 * ts_delta(high, 2))
            : 0
        """

    return (ts_delta(h, 2)
            .mul(-1)
            .where(ts_mean(h, 20) < h, 0)
            .stack('ticker')
            .swaplevel())

def alpha024(c):
    """((((ts_delta((ts_mean(close, 100)), 100) / ts_lag(close, 100)) <= 0.05)  
        ? (-1 * (close - ts_min(close, 100))) 
        : (-1 * ts_delta(close, 3)))
    """
    cond = ts_delta(ts_mean(c, 100), 100) / ts_lag(c, 100) <= 0.05

    return (c.sub(ts_min(c, 100)).mul(-1).where(cond, -ts_delta(c, 3))
            .stack('ticker')
            .swaplevel())

def alpha025(h, c, r, vwap, adv20):
    """rank((-1 * returns) * adv20 * vwap * (high - close))"""
    return (rank(-r.mul(adv20)
                 .mul(vwap)
                 .mul(h.sub(c)))
            .stack('ticker')
            .swaplevel())

def alpha026(h, v):
    """(-1 * ts_max(ts_corr(ts_rank(volume, 5), ts_rank(high, 5), 5), 3))"""
    return (ts_max(ts_corr(ts_rank(v, 5), 
                           ts_rank(h, 5), 5)
                   .replace([-np.inf, np.inf], np.nan), 3)
            .mul(-1)
            .stack('ticker')
            .swaplevel())

def alpha027(v, vwap):
    """((0.5 < rank(ts_mean(ts_corr(rank(volume), rank(vwap), 6), 2))) 
            ? -1
            : 1)"""
    cond = rank(ts_mean(ts_corr(rank(v),
                                rank(vwap), 6), 2))
    alpha = cond.notnull().astype(float)
    return (alpha.where(cond <= 0.5, -alpha)
            .stack('ticker')
            .swaplevel())

def alpha028(h, l, c, v, adv20):
    """scale(((ts_corr(adv20, low, 5) + (high + low) / 2) - close))"""
    return (scale(ts_corr(adv20, l, 5)
                  .replace([-np.inf, np.inf], 0)
                  .add(h.add(l).div(2).sub(c)))
            .stack('ticker')
            .swaplevel())

def alpha029(c, r):
    """(ts_min(ts_product(rank(rank(scale(log(ts_sum(ts_min(rank(rank((-1 * 
            rank(ts_delta((close - 1),5))))), 2), 1))))), 1), 5)
        + ts_rank(ts_lag((-1 * returns), 6), 5))
    """
    return (ts_min(rank(rank(scale(log(ts_sum(rank(rank(-rank(ts_delta((c - 1), 5)))), 2))))), 5)
            .add(ts_rank(ts_lag((-1 * r), 6), 5))
            .stack('ticker')
            .swaplevel())

def alpha030(c, v):
    """(((1.0 - rank(((sign((close - ts_lag(close, 1))) +
            sign((ts_lag(close, 1) - ts_lag(close, 2)))) +
            sign((ts_lag(close, 2) - ts_lag(close, 3)))))) *
            ts_sum(volume, 5)) / ts_sum(volume, 20))"""
    close_diff = ts_delta(c, 1)
    return (rank(sign(close_diff)
                 .add(sign(ts_lag(close_diff, 1)))
                 .add(sign(ts_lag(close_diff, 2))))
            .mul(-1).add(1)
            .mul(ts_sum(v, 5))
            .div(ts_sum(v, 20))
            .stack('ticker')
            .swaplevel())

def alpha031(l, c, adv20):
    """((rank(rank(rank(ts_weighted_mean((-1 * rank(rank(ts_delta(close, 10)))), 10)))) +
        rank((-1 * ts_delta(close, 3)))) + sign(scale(ts_corr(adv20, low, 12))))
    """
    return (rank(rank(rank(ts_weighted_mean(rank(rank(ts_delta(c, 10))).mul(-1), 10))))
            .add(rank(ts_delta(c, 3).mul(-1)))
            .add(sign(scale(ts_corr(adv20, l, 12)
                            .replace([-np.inf, np.inf],
                                     np.nan))))
            .stack('ticker')
            .swaplevel())

def alpha032(c, vwap):
    """scale(ts_mean(close, 7) - close) + 
        (20 * scale(ts_corr(vwap, ts_lag(close, 5),230)))"""
    return (scale(ts_mean(c, 7).sub(c))
            .add(20 * scale(ts_corr(vwap,
                                    ts_lag(c, 5), 230)))
            .stack('ticker')
            .swaplevel())

def alpha033(o, c):
    """rank(-(1 - (open / close)))"""
    return (rank(o.div(c).mul(-1).add(1).mul(-1))
            .stack('ticker')
            .swaplevel())

def alpha034(c, r):
    """rank(((1 - rank((ts_std(returns, 2) / ts_std(returns, 5)))) + (1 - rank(ts_delta(close, 1)))))"""

    return (rank(rank(ts_std(r, 2).div(ts_std(r, 5))
                      .replace([-np.inf, np.inf],
                               np.nan))
                 .mul(-1)
                 .sub(rank(ts_delta(c, 1)))
                 .add(2))
            .stack('ticker')
            .swaplevel())

def alpha035(h, l, c, v, r):
    """((ts_Rank(volume, 32) *
        (1 - ts_Rank(((close + high) - low), 16))) *
        (1 -ts_Rank(returns, 32)))
    """
    return (ts_rank(v, 32)
            .mul(1 - ts_rank(c.add(h).sub(l), 16))
            .mul(1 - ts_rank(r, 32))
            .stack('ticker')
            .swaplevel())

def alpha036(o, c, v, r, adv20):
    """2.21 * rank(ts_corr((close - open), ts_lag(volume, 1), 15)) +
        0.7 * rank((open- close)) +
        0.73 * rank(ts_Rank(ts_lag(-1 * returns, 6), 5)) +
        rank(abs(ts_corr(vwap,adv20, 6))) +
        0.6 * rank(((ts_mean(close, 200) - open) * (close - open)))
    """

    return (rank(ts_corr(c.sub(o), ts_lag(v, 1), 15)).mul(2.21)
            .add(rank(o.sub(c)).mul(.7))
            .add(rank(ts_rank(ts_lag(-r, 6), 5)).mul(0.73))
            .add(rank(abs(ts_corr(vwap, adv20, 6))))
            .add(rank(ts_mean(c, 200).sub(o).mul(c.sub(o))).mul(0.6))
            .stack('ticker')
            .swaplevel())

def alpha037(o, c):
    """(rank(ts_corr(ts_lag((open - close), 1), close, 200)) + rank((open - close)))"""
    return (rank(ts_corr(ts_lag(o.sub(c), 1), c, 200))
            .add(rank(o.sub(c)))
            .stack('ticker')
            .swaplevel())

def alpha038(o, c):
    """"-1 * rank(ts_rank(close, 10)) * rank(close / open)"""
    return (rank(ts_rank(o, 10))
            .mul(rank(c.div(o).replace([-np.inf, np.inf], np.nan)))
            .mul(-1)
            .stack('ticker')
            .swaplevel())

def alpha039(c, v, r, adv20):
    """-rank(ts_delta(close, 7) * (1 - rank(ts_weighted_mean(volume / adv20, 9)))) * 
            (1 + rank(ts_sum(returns, 250)))"""
    return (rank(ts_delta(c, 7).mul(rank(ts_weighted_mean(v.div(adv20), 9)).mul(-1).add(1))).mul(-1)
            .mul(rank(ts_mean(r, 250).add(1)))
            .stack('ticker')
            .swaplevel())

def alpha040(h, v):
    """((-1 * rank(ts_std(high, 10))) * ts_corr(high, volume, 10))
    """
    return (rank(ts_std(h, 10))
            .mul(ts_corr(h, v, 10))
            .mul(-1)
            .stack('ticker')
            .swaplevel())

def alpha041(h, l, vwap):
    """power(high * low, 0.5 - vwap"""
    return (power(h.mul(l), 0.5)
            .sub(vwap)
            .stack('ticker')
            .swaplevel())

def alpha042(c, vwap):
    """rank(vwap - close) / rank(vwap + close)"""
    return (rank(vwap.sub(c))
            .div(rank(vwap.add(c)))
            .stack('ticker')
            .swaplevel())

def alpha043(c, adv20):
    """(ts_rank((volume / adv20), 20) * ts_rank((-1 * ts_delta(close, 7)), 8))"""

    return (ts_rank(v.div(adv20), 20)
            .mul(ts_rank(ts_delta(c, 7).mul(-1), 8))
            .stack('ticker')
            .swaplevel())

def alpha044(h, v):
    """-ts_corr(high, rank(volume), 5)"""

    return (ts_corr(h, rank(v), 5)
            .replace([-np.inf, np.inf], np.nan)
            .mul(-1)
            .stack('ticker')
            .swaplevel())

def alpha045(c, v):
    """-(rank((ts_mean(ts_lag(close, 5), 20)) * 
        ts_corr(close, volume, 2)) *
        rank(ts_corr(ts_sum(close, 5), ts_sum(close, 20), 2)))"""

    return (rank(ts_mean(ts_lag(c, 5), 20))
            .mul(ts_corr(c, v, 2)
                 .replace([-np.inf, np.inf], np.nan))
            .mul(rank(ts_corr(ts_sum(c, 5),
                              ts_sum(c, 20), 2)))
            .mul(-1)
            .stack('ticker')
            .swaplevel())

def alpha046(c):
    """0.25 < ts_lag(ts_delta(close, 10), 10) / 10 - ts_delta(close, 10) / 10
            ? -1
            : ((ts_lag(ts_delta(close, 10), 10) / 10 - ts_delta(close, 10) / 10 < 0) 
                ? 1 
                : -ts_delta(close, 1))
    """

    cond = ts_lag(ts_delta(c, 10), 10).div(10).sub(ts_delta(c, 10).div(10))
    alpha = pd.DataFrame(-np.ones_like(cond),
                         index=c.index,
                         columns=c.columns)
    alpha[cond.isnull()] = np.nan
    return (cond.where(cond > 0.25,
                       -alpha.where(cond < 0,
                       -ts_delta(c, 1)))
            .stack('ticker')
            .swaplevel())

def alpha047(h, c, v, vwap, adv20):
    """((((rank((1 / close)) * volume) / adv20) * ((high * rank((high - close))) / 
        (ts_sum(high, 5) /5))) - rank((vwap - ts_lag(vwap, 5))))"""

    return (rank(c.pow(-1)).mul(v).div(adv20)
            .mul(h.mul(rank(h.sub(c))
                       .div(ts_mean(h, 5)))
                 .sub(rank(ts_delta(vwap, 5))))
            .stack('ticker')
            .swaplevel())

def alpha049(c):
    """ts_delta(ts_lag(close, 10), 10).div(10).sub(ts_delta(close, 10).div(10)) < -0.1 * c
        ? 1 
        : -ts_delta(close, 1)"""
    cond = (ts_delta(ts_lag(c, 10), 10).div(10)
            .sub(ts_delta(c, 10).div(10)) >= -0.1 * c)
    return (-ts_delta(c, 1)
            .where(cond, 1)
            .stack('ticker')
            .swaplevel())

def alpha050(v, vwap):
    """-ts_max(rank(ts_corr(rank(volume), rank(vwap), 5)), 5)"""
    return (ts_max(rank(ts_corr(rank(v),
                                rank(vwap), 5)), 5)
            .mul(-1)
            .stack('ticker')
            .swaplevel())

def alpha051(c):
    """ts_delta(ts_lag(close, 10), 10).div(10).sub(ts_delta(close, 10).div(10)) < -0.05 * c
        ? 1 
        : -ts_delta(close, 1)"""
    cond = (ts_delta(ts_lag(c, 10), 10).div(10)
            .sub(ts_delta(c, 10).div(10)) >= -0.05 * c)
    return (-ts_delta(c, 1)
            .where(cond, 1)
            .stack('ticker')
            .swaplevel())

def alpha052(l, v, r):
    """(ts_lag(ts_min(low, 5), 5) - ts_min(low, 5)) * 
        rank((ts_sum(returns, 240) - ts_sum(returns, 20)) / 220) * 
        ts_rank(volume, 5)
    """
    return (ts_delta(ts_min(l, 5), 5)
            .mul(rank(ts_sum(r, 240)
                      .sub(ts_sum(r, 20))
                      .div(220)))
            .mul(ts_rank(v, 5))
            .stack('ticker')
            .swaplevel())

def alpha053(h, l, c):
    """-1 * ts_delta(1 - (high - close) / (close - low), 9)"""
    inner = (c.sub(l)).add(1e-6)
    return (ts_delta(h.sub(c)
                     .mul(-1).add(1)
                     .div(c.sub(l)
                          .add(1e-6)), 9)
            .mul(-1)
            .stack('ticker')
            .swaplevel())

def alpha054(o, h, l, c):
    """-(low - close) * power(open, 5) / ((low - high) * power(close, 5))"""
    return (l.sub(c).mul(o.pow(5)).mul(-1)
            .div(l.sub(h).replace(0, -0.0001).mul(c ** 5))
            .stack('ticker')
            .swaplevel())

def alpha055(h, l, c):
    """(-1 * ts_corr(rank(((close - ts_min(low, 12)) / 
                            (ts_max(high, 12) - ts_min(low,12)))), 
                    rank(volume), 6))"""

    return (ts_corr(rank(c.sub(ts_min(l, 12))
                         .div(ts_max(h, 12).sub(ts_min(l, 12))
                              .replace(0, 1e-6))),
                    rank(v), 6)
            .replace([-np.inf, np.inf], np.nan)
            .mul(-1)
            .stack('ticker')
            .swaplevel())

def alpha056(r, cap):
    """-rank(ts_sum(returns, 10) / ts_sum(ts_sum(returns, 2), 3)) * 
        rank((returns * cap))
    """
    pass

def alpha057(c, vwap):
    """-(close - vwap) / ts_weighted_mean(rank(ts_argmax(close, 30)), 2)"""
    return (c.sub(vwap.add(1e-5))
            .div(ts_weighted_mean(rank(ts_argmax(c, 30)))).mul(-1)
            .stack('ticker')
            .swaplevel())

def alpha060(l, h, c, v):
    """-((2 * scale(rank(((((close - low) - (high - close)) / (high - low)) * volume)))) -scale(rank(ts_argmax(close, 10))))"""
    return (scale(rank(c.mul(2).sub(l).sub(h)
                       .div(h.sub(l).replace(0, 1e-5))
                       .mul(v))).mul(2)
            .sub(scale(rank(ts_argmax(c, 10)))).mul(-1)
            .stack('ticker')
            .swaplevel())

def alpha061(v, vwap):
    """rank((vwap - ts_min(vwap, 16))) < rank(ts_corr(vwap, adv180, 17))"""

    return (rank(vwap.sub(ts_min(vwap, 16)))
            .lt(rank(ts_corr(vwap, ts_mean(v, 180), 18)))
            .astype(int)
            .stack('ticker')
            .swaplevel())

def alpha062(o, h, l, vwap, adv20):
    """((rank(ts_corr(vwap, ts_sum(adv20, 22.4101), 9.91009)) < 
    rank(((rank(open) + rank(open)) < (rank(((high + low) / 2)) + rank(high))))) * -1)"""
    return (rank(ts_corr(vwap, ts_sum(adv20, 22), 9))
            .lt(rank(
                rank(o).mul(2))
                .lt(rank(h.add(l).div(2))
                    .add(rank(h))))
            .mul(-1)
            .stack('ticker')
            .swaplevel())

def alpha064(o, h, l, v, vwap):
    """((rank(ts_corr(ts_sum(((open * 0.178404) + (low * (1 - 0.178404))), 12.7054),ts_sum(adv120, 12.7054), 16.6208)) <
        rank(ts_delta(((((high + low) / 2) * 0.178404) + (vwap * (1 -0.178404))), 3.69741))) * -1)"""
    w = 0.178404
    return (rank(ts_corr(ts_sum(o.mul(w).add(l.mul(1 - w)), 12),
                         ts_sum(ts_mean(v, 120), 12), 16))
            .lt(rank(ts_delta(h.add(l).div(2).mul(w)
                               .add(vwap.mul(1 - w)), 3)))
            .mul(-1)
            .stack('ticker')
            .swaplevel())

def alpha065(o, v, vwap):
    """((rank(ts_corr(((open * 0.00817205) + (vwap * (1 - 0.00817205))), 
                        ts_sum(adv60,8.6911), 6.40374)) < 
        rank((open - ts_min(open, 13.635)))) * -1)
    """
    w = 0.00817205
    return (rank(ts_corr(o.mul(w).add(vwap.mul(1 - w)),
                         ts_mean(ts_mean(v, 60), 9), 6))
            .lt(rank(o.sub(ts_min(o, 13))))
            .mul(-1)
            .stack('ticker')
            .swaplevel())

def alpha066(l, h, vwap):
    """((rank(ts_weighted_mean(ts_delta(vwap, 3.51013), 7.23052)) +
        ts_rank(ts_weighted_mean(((((low* 0.96633) + (low *
                                    (1 - 0.96633))) - vwap) /
                                    (open - ((high + low) / 2))), 11.4157), 6.72611)) * -1)
    """
    w = 0.96633
    return (rank(ts_weighted_mean(ts_delta(vwap, 4), 7))
            .add(ts_rank(ts_weighted_mean(l.mul(w).add(l.mul(1 - w))
                                           .sub(vwap)
                                           .div(o.sub(h.add(l).div(2)).add(1e-3)), 11), 7))
            .mul(-1)
            .stack('ticker')
            .swaplevel())

def alpha067(h, v, sector, subindustry):
    """(power(rank((high - ts_min(high, 2.14593))),
        rank(ts_corr(IndNeutralize(vwap,IndClass.sector), 
                IndNeutralize(adv20, IndClass.subindustry), 6.02936))) * -1)
    """
    pass

def alpha068(h, c, v):
    """((ts_rank(ts_corr(rank(high), rank(adv15), 8.91644), 13.9333) <
        rank(ts_delta(((close * 0.518371) + (low * (1 - 0.518371))), 1.06157))) * -1)
    """
    w = 0.518371
    return (ts_rank(ts_corr(rank(h), rank(ts_mean(v, 15)), 9), 14)
            .lt(rank(ts_delta(c.mul(w).add(l.mul(1 - w)), 1)))
            .mul(-1)
            .stack('ticker')
            .swaplevel())

def alpha069(c, vwap, industry):
    """((power(rank(ts_max(ts_delta(IndNeutralize(vwap, IndClass.industry), 2.72412),4.79344)),
    Ts_Rank(ts_corr(((close * 0.490655) + (vwap * (1 - 0.490655))), adv20, 4.92416),9.0615))) * -1)
    """
    pass

def alpha076(c, v, vwap, industry):
    """((power(rank(ts_delta(vwap, 1.29456)),
        ts_rank(ts_corr(IndNeutralize(close, IndClass.industry), adv50, 17.8256), 17.9171))) * -1)
    """
    pass

def alpha071(o, c, v, vwap):
    """max(ts_rank(ts_weighted_mean(ts_corr(ts_rank(close, 3.43976), ts_rank(adv180,12.0647), 18.0175), 4.20501), 15.6948), 
            ts_rank(ts_weighted_mean((rank(((low + open) - (vwap +vwap)))^2), 16.4662), 4.4388))"""

    s1 = (ts_rank(ts_weighted_mean(ts_corr(ts_rank(c, 3),
                                           ts_rank(ts_mean(v, 180), 12), 18), 4), 16))
    s2 = (ts_rank(ts_weighted_mean(rank(l.add(o).
                                        sub(vwap.mul(2)))
                                   .pow(2), 16), 4))
    return (s1.where(s1 > s2, s2)
            .stack('ticker')
            .swaplevel())

def alpha072(h, l, v, vwap):
    """(rank(ts_weighted_mean(ts_corr(((high + low) / 2), adv40, 8.93345), 10.1519)) /
        rank(ts_weighted_mean(ts_corr(ts_rank(vwap, 3.72469), ts_rank(volume, 18.5188), 6.86671), 2.95011)))
    """
    return (rank(ts_weighted_mean(ts_corr(h.add(l).div(2), ts_mean(v, 40), 9), 10))
            .div(rank(ts_weighted_mean(ts_corr(ts_rank(vwap, 3), ts_rank(v, 18), 6), 2)))
            .stack('ticker')
            .swaplevel())

def alpha073(l, vwap):
    """(max(rank(ts_weighted_mean(ts_delta(vwap, 4.72775), 2.91864)),
        ts_rank(ts_weighted_mean(((ts_delta(((open * 0.147155) + 
            (low * (1 - 0.147155))), 2.03608) / 
            ((open *0.147155) + (low * (1 - 0.147155)))) * -1), 3.33829), 16.7411)) * -1)
        """
    w = 0.147155
    s1 = rank(ts_weighted_mean(ts_delta(vwap, 5), 3))
    s2 = (ts_rank(ts_weighted_mean(ts_delta(o.mul(w).add(l.mul(1 - w)), 2)
                                   .div(o.mul(w).add(l.mul(1 - w)).mul(-1)), 3), 16))

    print(s2)
    return (s1.where(s1 > s2, s2)
            .mul(-1)
            .stack('ticker')
            .swaplevel())

def alpha074(v, vwap):
    """((rank(ts_corr(close, ts_sum(adv30, 37.4843), 15.1365)) <
        rank(ts_corr(rank(((high * 0.0261661) + (vwap * (1 - 0.0261661)))), rank(volume), 11.4791)))* -1)"""

    w = 0.0261661
    return (rank(ts_corr(c, ts_mean(ts_mean(v, 30), 37), 15))
            .lt(rank(ts_corr(rank(h.mul(w).add(vwap.mul(1 - w))), rank(v), 11)))
            .mul(-1)
            .stack('ticker')
            .swaplevel())

def alpha075(l, v, vwap):
    """(rank(ts_corr(vwap, volume, 4.24304)) < 
        rank(ts_corr(rank(low), rank(adv50),12.4413)))
    """

    return (rank(ts_corr(vwap, v, 4))
            .lt(rank(ts_corr(rank(l), rank(ts_mean(v, 50)), 12)))
            .astype(int)
            .stack('ticker')
            .swaplevel())

def alpha076(l, vwap, sector):
    """(max(rank(ts_weighted_mean(ts_delta(vwap, 1.24383), 11.8259)),
            ts_rank(ts_weighted_mean(ts_rank(ts_corr(IndNeutralize(low, IndClass.sector), adv81,8.14941), 19.569), 17.1543), 19.383)) * -1)
    """
    pass

def alpha077(l, h, vwap):
    """min(rank(ts_weighted_mean(((((high + low) / 2) + high) - (vwap + high)), 20.0451)),
            rank(ts_weighted_mean(ts_corr(((high + low) / 2), adv40, 3.1614), 5.64125)))
    """

    s1 = rank(ts_weighted_mean(h.add(l).div(2).sub(vwap), 20))
    s2 = rank(ts_weighted_mean(ts_corr(h.add(l).div(2), ts_mean(v, 40), 3), 5))
    return (s1.where(s1 < s2, s2)
            .stack('ticker')
            .swaplevel())

def alpha078(l, v, vwap):
    """(rank(ts_corr(ts_sum(((low * 0.352233) + (vwap * (1 - 0.352233))), 19.7428),
        ts_sum(adv40, 19.7428), 6.83313))^rank(ts_corr(rank(vwap), rank(volume), 5.77492)))"""

    w = 0.352233
    return (rank(ts_corr(ts_sum((l.mul(w).add(vwap.mul(1 - w))), 19),
                         ts_sum(ts_mean(v, 40), 19), 6))
            .pow(rank(ts_corr(rank(vwap), rank(v), 5)))
            .stack('ticker')
            .swaplevel())

def alpha079(o, v, sector):
    """(rank(ts_delta(IndNeutralize(((close * 0.60733) + (open * (1 - 0.60733))),IndClass.sector), 1.23438)) < 
        rank(ts_corr(Ts_Rank(vwap, 3.60973), Ts_Rank(adv150,9.18637), 14.6644)))
    """
    pass

def alpha080(h, industry):
    """((power(rank(sign(ts_delta(IndNeutralize(((open * 0.868128) + (high * (1 - 0.868128))),IndClass.industry), 4.04545))),
        ts_rank(ts_corr(high, adv10, 5.11456), 5.53756)) * -1)
    """
    pass

def alpha081(v, vwap):
    """-(rank(log(ts_product(rank((rank(ts_corr(vwap, ts_sum(adv10, 49.6054),8.47743))^4)), 14.9655))) <
        rank(ts_corr(rank(vwap), rank(volume), 5.07914)))"""

    return (rank(log(ts_product(rank(rank(ts_corr(vwap,
                                                  ts_sum(ts_mean(v, 10), 50), 8))
                                     .pow(4)), 15)))
            .lt(rank(ts_corr(rank(vwap), rank(v), 5)))
            .mul(-1)
            .stack('ticker')
            .swaplevel())

def alpha082(o, v, sector):
    """(min(rank(ts_weighted_mean(ts_delta(open, 1.46063), 14.8717)),
        ts_rank(ts_weighted_mean(ts_corr(IndNeutralize(volume, IndClass.sector), 
        ((open * 0.634196) +(open * (1 - 0.634196))), 17.4842), 6.92131), 13.4283)) * -1)
    
    """
    pass

def alpha083(h, l, c):
    """(rank(ts_lag((high - low) / ts_mean(close, 5), 2)) * rank(rank(volume)) / 
            (((high - low) / ts_mean(close, 5) / (vwap - close)))
    """
    s = h.sub(l).div(ts_mean(c, 5))

    return (rank(rank(ts_lag(s, 2))
                 .mul(rank(rank(v)))
                 .div(s).div(vwap.sub(c).add(1e-3)))
            .stack('ticker')
            .swaplevel()
            .replace((np.inf, -np.inf), np.nan))

def alpha084(c, vwap):
    """power(ts_rank((vwap - ts_max(vwap, 15.3217)), 20.7127), 
        ts_delta(close,4.96796))"""
    return (rank(power(ts_rank(vwap.sub(ts_max(vwap, 15)), 20),
                       ts_delta(c, 6)))
            .stack('ticker')
            .swaplevel())

def alpha085(l, v):
    """power(rank(ts_corr(((high * 0.876703) + (close * (1 - 0.876703))), adv30,9.61331)),
        rank(ts_corr(ts_rank(((high + low) / 2), 3.70596), 
                     ts_rank(volume, 10.1595),7.11408)))
                     """
    w = 0.876703
    return (rank(ts_corr(h.mul(w).add(c.mul(1 - w)), ts_mean(v, 30), 10))
            .pow(rank(ts_corr(ts_rank(h.add(l).div(2), 4),
                              ts_rank(v, 10), 7)))
            .stack('ticker')
            .swaplevel())

def alpha086(c, v, vwap):
    """((ts_rank(ts_corr(close, ts_sum(adv20, 14.7444), 6.00049), 20.4195) < 
        rank(((open + close) - (vwap + open)))) * -1)
    """
    return (ts_rank(ts_corr(c, ts_mean(ts_mean(v, 20), 15), 6), 20)
            .lt(rank(c.sub(vwap)))
            .mul(-1)
            .stack('ticker')
            .swaplevel())

def alpha087(c, vwap, industry):
    """(max(rank(ts_weighted_mean(ts_delta(((close * 0.369701) + (vwap * (1 - 0.369701))),1.91233), 2.65461)), 
            ts_rank(ts_weighted_mean(abs(ts_corr(IndNeutralize(adv81,IndClass.industry), close, 13.4132)), 4.89768), 14.4535)) * -1)
    """
    pass

def alpha088(o, h, l, c, v):
    """min(rank(ts_weighted_mean(((rank(open) + rank(low)) - (rank(high) + rank(close))),8.06882)), 
        ts_rank(ts_weighted_mean(ts_corr(ts_rank(close, 8.44728), 
                ts_rank(adv60,20.6966), 8.01266), 6.65053), 2.61957))"""

    s1 = (rank(ts_weighted_mean(rank(o)
                                .add(rank(l))
                                .sub(rank(h))
                                .add(rank(c)), 8)))
    s2 = ts_rank(ts_weighted_mean(ts_corr(ts_rank(c, 8),
                                          ts_rank(ts_mean(v, 60), 20), 8), 6), 2)

    return (s1.where(s1 < s2, s2)
            .stack('ticker')
            .swaplevel())

def alpha089(l, v, vwap, industry):
    """(ts_rank(ts_weighted_mean(ts_corr(((low * 0.967285) + 
        (low * (1 - 0.967285))), adv10,6.94279), 5.51607), 3.79744) - 
        ts_rank(ts_weighted_mean(ts_delta(IndNeutralize(vwap,IndClass.industry), 3.48158), 10.1466), 15.3012))
    """
    pass

def alpha090(c, l, subindustry):
    """((rank((close - ts_max(close, 4.66719)))
        ^ts_rank(ts_corr(IndNeutralize(adv40,IndClass.subindustry), low, 5.38375), 3.21856)) * -1)
    """
    pass

def alpha091(v, vwap, industry):
    """((ts_rank(ts_weighted_mean(ts_weighted_mean(ts_corr(IndNeutralize(close,IndClass.industry), volume, 9.74928), 16.398), 3.83219), 4.8667) -
        rank(ts_weighted_mean(ts_corr(vwap, adv30, 4.01303), 2.6809))) * -1)
    """
    pass

def alpha092(o, l, c, v):
    """min(ts_rank(ts_weighted_mean(((((high + low) / 2) + close) < (low + open)), 14.7221),18.8683), 
            ts_rank(ts_weighted_mean(ts_corr(rank(low), rank(adv30), 7.58555), 6.94024),6.80584))
    """
    p1 = ts_rank(ts_weighted_mean(h.add(l).div(2).add(c).lt(l.add(o)), 15), 18)
    p2 = ts_rank(ts_weighted_mean(ts_corr(rank(l), rank(ts_mean(v, 30)), 7), 6), 6)

    return (p1.where(p1<p2, p2)
            .stack('ticker')
            .swaplevel())

def alpha093(c, v, vwap, industry):
    """(ts_rank(ts_weighted_mean(ts_corr(IndNeutralize(vwap, IndClass.industry), adv81,17.4193), 19.848), 7.54455) / 
        rank(ts_weighted_mean(ts_delta(((close * 0.524434) + (vwap * (1 -0.524434))), 2.77377), 16.2664)))
    """
    pass

def alpha094(v, vwap):
    """((rank((vwap - ts_min(vwap, 11.5783)))^ts_rank(ts_corr(ts_rank(vwap,19.6462), 
        ts_rank(adv60, 4.02992), 18.0926), 2.70756)) * -1)
    """

    return (rank(vwap.sub(ts_min(vwap, 11)))
            .pow(ts_rank(ts_corr(ts_rank(vwap, 20),
                                 ts_rank(ts_mean(v, 60), 4), 18), 2))
            .mul(-1)
            .stack('ticker')
            .swaplevel())

def alpha095(o, l, v):
    """(rank((open - ts_min(open, 12.4105))) < 
        ts_rank((rank(ts_corr(ts_sum(((high + low)/ 2), 19.1351), ts_sum(adv40, 19.1351), 12.8742))^5), 11.7584))
    """
    
    return (rank(o.sub(ts_min(o, 12)))
            .lt(ts_rank(rank(ts_corr(ts_mean(h.add(l).div(2), 19),
                                     ts_sum(ts_mean(v, 40), 19), 13).pow(5)), 12))
            .astype(int)
            .stack('ticker')
            .swaplevel())

def alpha096(c, v, vwap):
    """(max(ts_rank(ts_weighted_mean(ts_corr(rank(vwap), rank(volume), 5.83878),4.16783), 8.38151), 
        ts_rank(ts_weighted_mean(ts_argmax(ts_corr(ts_rank(close, 7.45404), ts_rank(adv60, 4.13242), 3.65459), 12.6556), 14.0365), 13.4143)) * -1)"""
    
    s1 = ts_rank(ts_weighted_mean(ts_corr(rank(vwap), rank(v), 10), 4), 8)
    s2 = ts_rank(ts_weighted_mean(ts_argmax(ts_corr(ts_rank(c, 7),
                                                    ts_rank(ts_mean(v, 60), 10), 10), 12), 14), 13)
    return (s1.where(s1 > s2, s2)
            .mul(-1)
            .stack('ticker')
            .swaplevel())

def alpha097(l):
    """((rank(ts_weighted_mean(ts_delta(IndNeutralize(((low * 0.721001) + 
        (vwap * (1 - 0.721001))),IndClass.industry), 3.3705), 20.4523)) - 
        ts_rank(ts_weighted_mean(ts_rank(ts_corr(Ts_Rank(low,7.87871), 
        ts_rank(adv60, 17.255), 4.97547), 18.5925), 15.7152), 6.71659)) * -1)
    """
    pass

def alpha098(o, v, vwap):
    """(rank(ts_weighted_mean(ts_corr(vwap, ts_sum(adv5, 26.4719), 4.58418), 7.18088)) -
        rank(ts_weighted_mean(ts_tank(ts_argmin(ts_corr(rank(open), 
        rank(adv15), 20.8187), 8.62571),6.95668), 8.07206)))
    """
    adv5 = ts_mean(v, 5)
    adv15 = ts_mean(v, 15)
    return (rank(ts_weighted_mean(ts_corr(vwap, ts_mean(adv5, 26), 4), 7))
            .sub(rank(ts_weighted_mean(ts_rank(ts_argmin(ts_corr(rank(o),
                                                                 rank(adv15), 20), 8), 6))))
            .stack('ticker')
            .swaplevel())

def alpha099(l, v):
    """((rank(ts_corr(ts_sum(((high + low) / 2), 19.8975), 
                    ts_sum(adv60, 19.8975), 8.8136)) <
                    rank(ts_corr(low, volume, 6.28259))) * -1)"""

    return ((rank(ts_corr(ts_sum((h.add(l).div(2)), 19),
                          ts_sum(ts_mean(v, 60), 19), 8))
             .lt(rank(ts_corr(l, v, 6)))
             .mul(-1))
            .stack('ticker')
            .swaplevel())

def alpha100(r, cap):
    """(0 - (1 * (((1.5 * scale(indneutralize(
                indneutralize(rank(((((close - low) - (high -close)) / (high - low)) * volume)), 
                                IndClass.subindustry), IndClass.subindustry))) - 
    scale(indneutralize((ts_corr(close, rank(adv20), 5) - rank(ts_argmin(close, 30))), IndClass.subindustry))) * (volume / adv20))))
    """
    pass

def alpha101(o, h, l, c):
    """((close - open) / ((high - low) + .001))"""
    return (c.sub(o).div(h.sub(l).add(1e-3))
            .stack('ticker')
            .swaplevel())

In [16]:
# Fixes / missing alpha implementations for our environment
# - ML4T notebook left some alphas as `pass` or used non-3-digit names.
# - We implement them here directly from `101_alphas.pdf`.

import numpy as np
import pandas as pd


def _w(d: float) -> int:
    return max(1, int(round(float(d))))


def indneutralize(x: pd.DataFrame, _group=None) -> pd.DataFrame:
    # No industry/sector data available: neutralize vs full universe
    return x.sub(x.mean(axis=1), axis=0)

# Alias used in some formulas
IndNeutralize = indneutralize


def alpha048(c, h, l, v, vwap):
    dc = ts_delta(c, 1)
    dc_lag = ts_lag(dc, 1)
    corr = ts_corr(dc, dc_lag, 250)
    num = indneutralize((corr * dc) / c)
    den = ts_sum((dc / ts_lag(c, 1)) ** 2, 250)
    return num / den


def alpha056(r, cap):
    term1 = rank(ts_sum(r, 10) / ts_sum(ts_sum(r, 2), 3))
    term2 = rank(r * cap)
    return -1.0 * term1 * term2


def alpha058(vwap, v):
    x = ts_corr(indneutralize(vwap), v, _w(3.92795))
    y = decay_linear(x, _w(7.89291))
    return -1.0 * ts_rank(y, _w(5.50322))


def alpha059(vwap, v):
    x = ts_corr(indneutralize(vwap), v, _w(4.25197))
    y = decay_linear(x, _w(16.2289))
    return -1.0 * ts_rank(y, _w(8.19648))


def alpha063(c, o, vwap, adv180):
    term1 = rank(decay_linear(ts_delta(indneutralize(c), _w(2.25164)), _w(8.22237)))
    x = (vwap * 0.318108) + (o * (1.0 - 0.318108))
    y = ts_sum(adv180, _w(37.2467))
    term2 = rank(decay_linear(ts_corr(x, y, _w(13.557)), _w(12.2883)))
    return (term2 - term1)


def alpha067(h, vwap, adv20):
    a = rank(h - ts_min(h, _w(2.14593)))
    b = rank(ts_corr(indneutralize(vwap), indneutralize(adv20), _w(6.02936)))
    return -1.0 * a.pow(b)


def alpha069(c, vwap, adv20):
    a = rank(ts_max(ts_delta(indneutralize(vwap), _w(2.72412)), _w(4.79344)))
    x = (c * 0.490655) + (vwap * (1.0 - 0.490655))
    b = ts_rank(ts_corr(x, adv20, _w(4.92416)), _w(9.0615))
    return -1.0 * a.pow(b)


def alpha070(c, vwap, adv50):
    a = rank(ts_delta(vwap, _w(1.29456)))
    b = ts_rank(ts_corr(indneutralize(c), adv50, _w(17.8256)), _w(17.9171))
    return -1.0 * a.pow(b)


def alpha076(o, l, vwap, adv81):
    term1 = rank(decay_linear(ts_delta(vwap, _w(1.24383)), _w(11.8259)))
    x = ts_rank(ts_corr(indneutralize(l), adv81, _w(8.14941)), _w(19.569))
    term2 = ts_rank(decay_linear(x, _w(17.1543)), _w(19.383))
    return -1.0 * term1.where(term1 >= term2, term2)


def alpha079(c, o, vwap, adv150):
    x = indneutralize((c * 0.60733) + (o * (1.0 - 0.60733)))
    left = rank(ts_delta(x, _w(1.23438)))
    right = rank(ts_corr(ts_rank(vwap, _w(3.60973)), ts_rank(adv150, _w(9.18637)), _w(14.6644)))
    return (left < right).astype(float)


def alpha080(o, h, adv10):
    x = indneutralize((o * 0.868128) + (h * (1.0 - 0.868128)))
    a = rank(np.sign(ts_delta(x, _w(4.04545))))
    b = ts_rank(ts_corr(h, adv10, _w(5.11456)), _w(5.53756))
    return -1.0 * a.pow(b)



def alpha082(o, v):
    term1 = rank(decay_linear(ts_delta(o, _w(1.46063)), _w(14.8717)))
    term2 = ts_rank(decay_linear(ts_corr(indneutralize(v), o, _w(17.4842)), _w(6.92131)), _w(13.4283))
    return -1.0 * term1.where(term1 <= term2, term2)


def alpha087(c, vwap, adv81):
    x = (c * 0.369701) + (vwap * (1.0 - 0.369701))
    term1 = rank(decay_linear(ts_delta(x, _w(1.91233)), _w(2.65461)))
    term2 = ts_rank(decay_linear(abs(ts_corr(indneutralize(adv81), c, _w(13.4132))), _w(4.89768)), _w(14.4535))
    return -1.0 * term1.where(term1 >= term2, term2)


def alpha089(l, vwap, adv10):
    term1 = ts_rank(decay_linear(ts_corr(l, adv10, _w(6.94279)), _w(5.51607)), _w(3.79744))
    term2 = ts_rank(decay_linear(ts_delta(indneutralize(vwap), _w(3.48158)), _w(10.1466)), _w(15.3012))
    return term1 - term2


def alpha090(c, l, adv40):
    a = rank(c - ts_max(c, _w(4.66719)))
    b = ts_rank(ts_corr(indneutralize(adv40), l, _w(5.38375)), _w(3.21856))
    return -1.0 * a.pow(b)


def alpha091(c, v, vwap, adv30):
    term1 = ts_rank(decay_linear(decay_linear(ts_corr(indneutralize(c), v, _w(9.74928)), _w(16.398)), _w(3.83219)), _w(4.8667))
    term2 = rank(decay_linear(ts_corr(vwap, adv30, _w(4.01303)), _w(2.6809)))
    return (term2 - term1)


def alpha093(c, vwap, adv81):
    num = ts_rank(decay_linear(ts_corr(indneutralize(vwap), adv81, _w(17.4193)), _w(19.848)), _w(7.54455))
    den = rank(decay_linear(ts_delta((c * 0.524434) + (vwap * (1.0 - 0.524434)), _w(2.77377)), _w(16.2664)))
    return num / den


def alpha097(l, vwap, adv60):
    x = indneutralize((l * 0.721001) + (vwap * (1.0 - 0.721001)))
    term1 = rank(decay_linear(ts_delta(x, _w(3.3705)), _w(20.4523)))
    inner = ts_corr(ts_rank(l, _w(7.87871)), ts_rank(adv60, _w(17.255)), _w(4.97547))
    term2 = ts_rank(decay_linear(ts_rank(inner, _w(18.5925)), _w(15.7152)), _w(6.71659))
    return (term2 - term1)


def alpha100(c, h, l, v, adv20):
    expr = (((c - l) - (h - c)) / (h - l)) * v
    term1 = 1.5 * scale(indneutralize(indneutralize(rank(expr))))
    term2 = scale(indneutralize(ts_corr(c, rank(adv20), 5) - rank(ts_argmin(c, 30))))
    return -1.0 * (term1 - term2) * (v / adv20)

# (No compatibility wrappers; we implement the padded alphaXXX names directly.)


In [17]:
# Backtest helpers

def alpha_to_matrix(out):
    # ML4T alpha functions often return a MultiIndex Series (date, ticker) or (ticker, date)
    if isinstance(out, pd.Series) and isinstance(out.index, pd.MultiIndex):
        idx_names = [n for n in out.index.names if n is not None]
        if 'ticker' in out.index.names:
            df = out.unstack('ticker')
        else:
            df = out.unstack()
        # Ensure datetime index
        if not isinstance(df.index, pd.DatetimeIndex):
            # if tickers became index, transpose
            if isinstance(df.columns, pd.DatetimeIndex):
                df = df.T
        return df.sort_index()

    if isinstance(out, pd.DataFrame):
        return out.sort_index()

    if isinstance(out, pd.Series):
        return out.to_frame('value').sort_index()

    raise TypeError(f'Unsupported alpha output type: {type(out)}')


def scores_to_weights(scores: pd.DataFrame) -> pd.DataFrame:
    s = scores.replace([np.inf, -np.inf], np.nan)
    s = s.sub(s.mean(axis=1), axis=0)
    denom = s.abs().sum(axis=1).replace(0.0, np.nan)
    w = s.div(denom, axis=0).fillna(0.0)
    return w

cfg = BacktestConfig(initial_equity=1_000_000.0, transaction_cost_bps=5.0, mode='vectorized', allow_leverage=True)
output_notebook()


Loading BokehJS ...

In [18]:
import inspect


In [19]:
# Run all 101 alphas

reports = []

for n in range(1, 102):
    name = f'alpha{n:03d}'
    f = globals().get(name)
    if f is None:
        raise KeyError(f'Missing {name}')

    # Build kwargs by signature
    sig = inspect.signature(f)
    kwargs = {}
    for p in sig.parameters:
        if p in globals():
            kwargs[p] = globals()[p]
        else:
            raise KeyError(f'{name} requires {p} but it is not defined')

    out = f(**kwargs)
    scores = alpha_to_matrix(out)
    weights = scores_to_weights(scores).reindex(close.index).fillna(0.0)

    # Slice to overlap window
    close_bt = close.reindex(weights.index)

    res = run_backtest(close_bt, weights, config=cfg)
    report = compute_backtest_report(result=res, close_prices=close_bt)

    reports.append(report.rename(f'{n:03d}'))
    display(report.to_frame(f'Alpha {n:03d}'))

    layout = build_interactive_portfolio_layout(
        market_ohlcv=market_df,
        equity=res.equity,
        returns=res.returns,
        weights=res.weights,
        turnover=res.turnover,
        costs=res.costs,
        close_prices=close_bt,
        title=f'Alpha {n:03d}',
    )
    show(layout)

# Combined report table
all_reports = pd.DataFrame(reports)
display(all_reports)


Alpha 001
Start                       2016-02-22 00:00:00
End                         2026-01-16 00:00:00
Duration                     3616 days 00:00:00
Initial Equity                         999500.0
Final Equity                      324625.149129
Equity Peak                            999500.0
Total Return [%]                     -67.521246
CAGR [%]                             -10.753469
Volatility (ann) [%]                   5.325024
Sharpe                                -2.109452
Sortino                               -3.186409
Max Drawdown [%]                     -67.575958
Calmar                                -0.159132
Best Day [%]                           2.732657
Worst Day [%]                         -2.637542
Avg Gross Exposure                          1.0
Avg Net Exposure                            0.0
Exposure Time [%]                         100.0
Rebalance Days                             2487
Total Turnover                      2246.866311
Avg Daily Turnover                     0.901632
Transaction Cost (bps)                      5.0
Total Costs                            1.123433
Costs / Initial Equity [%]             0.000112
Benchmark Total Return [%]           513.622312
Benchmark CAGR [%]                    20.145465

Alpha 002
Start                       2016-02-17 00:00:00
End                         2026-01-16 00:00:00
Duration                     3621 days 00:00:00
Initial Equity                         999500.0
Final Equity                      482710.904501
Equity Peak                      1029151.822894
Total Return [%]                     -51.704762
CAGR [%]                              -7.090334
Volatility (ann) [%]                    3.28565
Sharpe                                -2.222187
Sortino                               -3.465963
Max Drawdown [%]                     -53.099686
Calmar                                -0.133529
Best Day [%]                           2.022931
Worst Day [%]                         -0.941466
Avg Gross Exposure                     0.999599
Avg Net Exposure                           -0.0
Exposure Time [%]                      99.95992
Rebalance Days                             2495
Total Turnover                      1460.761663
Avg Daily Turnover                     0.585476
Transaction Cost (bps)                      5.0
Total Costs                            0.730381
Costs / Initial Equity [%]             0.000073
Benchmark Total Return [%]           520.313067
Benchmark CAGR [%]                    20.250639

Alpha 003
Start                       2016-02-05 00:00:00
End                         2026-01-16 00:00:00
Duration                     3633 days 00:00:00
Initial Equity                         999500.0
Final Equity                      450519.658367
Equity Peak                            999500.0
Total Return [%]                     -54.925497
CAGR [%]                              -7.715197
Volatility (ann) [%]                   3.677399
Sharpe                                -2.165121
Sortino                               -3.349332
Max Drawdown [%]                      -55.04658
Calmar                                -0.140158
Best Day [%]                           1.659786
Worst Day [%]                         -1.660499
Avg Gross Exposure                          1.0
Avg Net Exposure                            0.0
Exposure Time [%]                         100.0
Rebalance Days                             2502
Total Turnover                      1203.493104
Avg Daily Turnover                     0.481012
Transaction Cost (bps)                      5.0
Total Costs                            0.601747
Costs / Initial Equity [%]              0.00006
Benchmark Total Return [%]           540.285407
Benchmark CAGR [%]                     20.57297

Alpha 004
Start                       2016-02-04 00:00:00
End                         2026-01-16 00:00:00
Duration                     3634 days 00:00:00
Initial Equity                         999500.0
Final Equity                      385314.327583
Equity Peak                      1009750.257866
Total Return [%]                     -61.449292
CAGR [%]                              -9.154082
Volatility (ann) [%]                   5.676416
Sharpe                                -1.662835
Sortino                               -2.641455
Max Drawdown [%]                     -61.840631
Calmar                                -0.148027
Best Day [%]                           2.818591
Worst Day [%]                         -2.249072
Avg Gross Exposure                          1.0
Avg Net Exposure                            0.0
Exposure Time [%]                         100.0
Rebalance Days                             2503
Total Turnover                       1598.67099
Avg Daily Turnover                     0.638702
Transaction Cost (bps)                      5.0
Total Costs                            0.799335
Costs / Initial Equity [%]              0.00008
Benchmark Total Return [%]           525.656265
Benchmark CAGR [%]                    20.283618

Alpha 005
Start                       2016-02-05 00:00:00
End                         2026-01-16 00:00:00
Duration                     3633 days 00:00:00
Initial Equity                         999500.0
Final Equity                       258337.16664
Equity Peak                      1000579.246071
Total Return [%]                      -74.15336
CAGR [%]                             -12.744258
Volatility (ann) [%]                   5.463207
Sharpe                                -2.467293
Sortino                               -3.775309
Max Drawdown [%]                     -74.549016
Calmar                                -0.170951
Best Day [%]                           2.068728
Worst Day [%]                         -2.357767
Avg Gross Exposure                          1.0
Avg Net Exposure                            0.0
Exposure Time [%]                         100.0
Rebalance Days                             2502
Total Turnover                      2243.796232
Avg Daily Turnover                     0.896801
Transaction Cost (bps)                      5.0
Total Costs                            1.121898
Costs / Initial Equity [%]             0.000112
Benchmark Total Return [%]           540.285407
Benchmark CAGR [%]                     20.57297

...

Alpha 013
Start                       2016-01-29 00:00:00
End                         2026-01-16 00:00:00
Duration                     3640 days 00:00:00
Initial Equity                         999500.0
Final Equity                      462959.868538
Equity Peak                      1001012.055764
Total Return [%]                     -53.680854
CAGR [%]                               -7.44725
Volatility (ann) [%]                    3.07151
Sharpe                                -2.504522
Sortino                               -3.615837
Max Drawdown [%]                      -53.75082
Calmar                                -0.138551
Best Day [%]                           1.158157
Worst Day [%]                         -2.515378
Avg Gross Exposure                     0.998006
Avg Net Exposure                            0.0
Exposure Time [%]                     99.800558
Rebalance Days                             2504
Total Turnover                      1536.905467
Avg Daily Turnover                     0.613046
Transaction Cost (bps)                      5.0
Total Costs                            0.768453
Costs / Initial Equity [%]             0.000077
Benchmark Total Return [%]           518.255896
Benchmark CAGR [%]                    20.104373

Alpha 014
Start                       2016-02-05 00:00:00
End                         2026-01-16 00:00:00
Duration                     3633 days 00:00:00
Initial Equity                         999500.0
Final Equity                      293740.411341
Equity Peak                      1002958.509312
Total Return [%]                     -70.611264
CAGR [%]                             -11.607774
Volatility (ann) [%]                   5.209664
Sharpe                                -2.341809
Sortino                               -3.536262
Max Drawdown [%]                     -71.126833
Calmar                                -0.163198
Best Day [%]                           3.414846
Worst Day [%]                         -2.544286
Avg Gross Exposure                          1.0
Avg Net Exposure                           -0.0
Exposure Time [%]                         100.0
Rebalance Days                             2502
Total Turnover                      2222.535875
Avg Daily Turnover                     0.888304
Transaction Cost (bps)                      5.0
Total Costs                            1.111268
Costs / Initial Equity [%]             0.000111
Benchmark Total Return [%]           540.285407
Benchmark CAGR [%]                     20.57297

Alpha 015
Start                       2016-01-29 00:00:00
End                         2026-01-16 00:00:00
Duration                     3640 days 00:00:00
Initial Equity                         999500.0
Final Equity                       190676.28489
Equity Peak                      1004191.164497
Total Return [%]                     -80.922833
CAGR [%]                             -15.345619
Volatility (ann) [%]                   6.415513
Sharpe                                 -2.56349
Sortino                               -3.779597
Max Drawdown [%]                     -81.209105
Calmar                                -0.188964
Best Day [%]                           1.933563
Worst Day [%]                         -2.955311
Avg Gross Exposure                          1.0
Avg Net Exposure                            0.0
Exposure Time [%]                         100.0
Rebalance Days                             2507
Total Turnover                      2610.389708
Avg Daily Turnover                      1.04124
Transaction Cost (bps)                      5.0
Total Costs                            1.305195
Costs / Initial Equity [%]             0.000131
Benchmark Total Return [%]           518.255896
Benchmark CAGR [%]                    20.104373

Alpha 016
Start                       2016-01-29 00:00:00
End                         2026-01-16 00:00:00
Duration                     3640 days 00:00:00
Initial Equity                         999500.0
Final Equity                      362248.642851
Equity Peak                       999900.663111
Total Return [%]                     -63.757014
CAGR [%]                              -9.702411
Volatility (ann) [%]                   3.054538
Sharpe                                  -3.3256
Sortino                               -4.903172
Max Drawdown [%]                     -63.810937
Calmar                                -0.152049
Best Day [%]                           0.977177
Worst Day [%]                          -1.16431
Avg Gross Exposure                          1.0
Avg Net Exposure                            0.0
Exposure Time [%]                         100.0
Rebalance Days                             2507
Total Turnover                      1694.676167
Avg Daily Turnover                     0.675978
Transaction Cost (bps)                      5.0
Total Costs                            0.847338
Costs / Initial Equity [%]             0.000085
Benchmark Total Return [%]           518.255896
Benchmark CAGR [%]                    20.104373

KeyboardInterrupt: 